## Imports

In [1]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from sklearn.preprocessing import MinMaxScaler
import plotly.express as px

## Dados

In [2]:
rooms_df = pd.read_csv("../data/clean_data/rooms_clean.csv", sep=';')
rooms_df['latitude'] = rooms_df['latitude'].astype(str).str.replace(',', '.', regex=False).astype(float)
rooms_df['longitude'] = rooms_df['longitude'].astype(str).str.replace(',', '.', regex=False).astype(float)

In [3]:
reviews_df = pd.read_csv("../data/clean_data/reviews_clean.csv", sep=';')

In [4]:
df_rooms_reviews = pd.merge(
    rooms_df,
    reviews_df,
    on='id',
    how='inner',
    suffixes=('_rooms', '_reviews')
)

df_reviews_rooms = pd.merge(
    reviews_df,
    rooms_df,
    on='id',
    how='inner',
    suffixes=('_rooms', '_reviews')
)

In [5]:
PALETA_THEME_COLORS = ['#feaf88', '#ff687d', '#cb6686', '#745984', '#265d84']
PALETA_AIRBNB_COLORS = ['#fb5c62', '#faeeed', '#ec9a9d', '#f5abb4', '#e9838c']

## Mapa

In [6]:
fig_map = px.scatter_mapbox(
    df_rooms_reviews,
    lat="latitude",
    lon="longitude",
    color="neighbourhood_group",
    size="price",
    size_max=20,
    hover_name="name",
    hover_data={
        "neighbourhood_group": True,
        "price": True,
        "room_type": True
    },
    color_discrete_sequence=PALETA_THEME_COLORS,
    zoom=9,
    height=650,
    title="Quartos distribuídos por Nova York"
)

fig_map.update_layout(
    mapbox_style="carto-positron",
    font=dict(
        family="Fira Sans, Roboto, Arial",
        size=14,
        color="#2e2e2e"
    ),
    title_font=dict(
        family="Fira Sans, Roboto, Arial",
        size=20,
        color="#111111"
    ),
    margin=dict(l=0, r=0, t=60, b=0)
)

fig_map.show()

C:\Users\Vitoria\AppData\Local\Temp\ipykernel_23528\3232749344.py:1: DeprecationWarning: *scatter_mapbox* is deprecated! Use *scatter_map* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/
  fig_map = px.scatter_mapbox(


In [7]:
fig_map.write_image("../results/presentation_figures/mapa_airbnb_ny.png", scale=3)

## Graficos de coluna

In [8]:
df_neighbourhood = (
    df_rooms_reviews.groupby("neighbourhood_group", as_index=False)
    .agg(qtd_quartos=("id", "count"))
    .sort_values(by="qtd_quartos", ascending=False)
)

fig_neighbourhood_group = px.bar(
    df_neighbourhood,
    y="neighbourhood_group",
    x="qtd_quartos",
    color="neighbourhood_group",
    color_discrete_sequence=PALETA_THEME_COLORS,
    title="Quantidade de quartos por bairro principal (Nova York)"
)
fig_neighbourhood_group.update_traces(
    marker_line_width=0,
    opacity=1,
    text=None
)
fig_neighbourhood_group.update_layout(
    height=600,
    font=dict(
        family="Fira Sans, Roboto, Arial",
        size=14,
        color="#2e2e2e"
    ),
    title_font=dict(
        family="Fira Sans, Roboto, Arial",
        size=20,
        color="#111111"
    ),
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
    yaxis=dict(
        title="Bairro Principal",
        showgrid=False,
        zeroline=False,
        linecolor="#CCCCCC",
        tickfont=dict(size=12)
    ),
    xaxis=dict(
        title="Quantidade de Quartos",
        showgrid=False,
        zeroline=False,
        linecolor="#CCCCCC",
        tickfont=dict(size=12),
        showticklabels=True
    ),
    margin=dict(l=60, r=40, t=60, b=60),
    showlegend=False
)

fig_neighbourhood_group.show()

In [9]:
fig_neighbourhood_group.write_image("../results/presentation_figures/neighbourhood_group_bar.png", scale=3)

In [10]:
df_rooms_reviews['tipo_quarto'] = df_rooms_reviews['room_type'].replace({
    'Entire home/apt': 'Casa/apt inteiro',
    'Private room': 'Quarto privado',
    'Shared room': 'Quarto compartilhado'
})

bins = [0, 100, 300, 10000]  # ajuste conforme sua realidade
labels = ['Econômico', 'Intermediário', 'Luxo']
df_rooms_reviews['categoria_preco'] = pd.cut(df_rooms_reviews['price'], bins=bins, labels=labels, include_lowest=True)


df_roomtype = (
    df_rooms_reviews.groupby(['tipo_quarto', 'categoria_preco'], as_index=False)
    .agg(qtd=('id', 'count'))
)
df_roomtype['percentual'] = (
    df_roomtype.groupby('tipo_quarto')['qtd']
    .transform(lambda x: (x / x.sum()) * 100)
)

tipo_order = ['Casa/apt inteiro', 'Quarto privado', 'Quarto compartilhado']
cat_order = ['Econômico', 'Intermediário', 'Luxo']

C:\Users\Vitoria\AppData\Local\Temp\ipykernel_23528\4183168258.py:13: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.



In [11]:
def aplicar_estilo_minimalista(fig, percentual=False):
    """Aplica estilo padronizado aos gráficos Plotly"""
    fig.update_traces(marker_line_width=0, opacity=1)
    
    fig.update_layout(
        height=800,
        width=800,
        font=dict(family="Fira Sans, Roboto, Arial", size=15, color="#2e2e2e"),
        title_font=dict(family="Fira Sans, Roboto, Arial", size=20, color="#111111"),
        paper_bgcolor='rgba(0,0,0,0)',
        plot_bgcolor='rgba(0,0,0,0)',
        bargap=0.25,
        xaxis=dict(
            title=None,
            showgrid=True,
            gridcolor="#E5E5E5",
            zeroline=False,
            tickformat=".0f" if percentual else "~s",
            range=[0, 100] if percentual else None
        ),
        yaxis=dict(title=None, showgrid=False, zeroline=False, visible=False),
        legend=dict(
            orientation="h",
            yanchor="bottom",
            y=1.05,
            xanchor="right",
            x=1,
            title=None,
            font=dict(size=14)
        ),
        margin=dict(l=80, r=40, t=70, b=40)
    )
    return fig

In [12]:
fig_roomtype_quant = px.bar(
    df_roomtype,
    y='tipo_quarto',
    x='qtd',
    color='categoria_preco',
    category_orders={'tipo_quarto': tipo_order, 'categoria_preco': cat_order},
    color_discrete_sequence=PALETA_THEME_COLORS,
    title="Tipo de quarto por categoria de preço",
    orientation='h'
)
fig_roomtype_quant = aplicar_estilo_minimalista(fig_roomtype_quant)

In [13]:
fig_roomtype_percentual = px.bar(
    df_roomtype,
    y='tipo_quarto',
    x='percentual',
    color='categoria_preco',
    category_orders={'tipo_quarto': tipo_order, 'categoria_preco': cat_order},
    color_discrete_sequence=PALETA_THEME_COLORS,
    title="Distribuição percentual de tipos de quarto por categoria de preço",
    orientation='h',
    text=df_roomtype['percentual'].apply(lambda x: f"{x:.1f}%")
)

fig_roomtype_percentual.update_traces(
    textposition="inside",
    insidetextanchor="middle",
    textfont=dict(color="white", size=16)
)
fig_roomtype_percentual = aplicar_estilo_minimalista(fig_roomtype_percentual, percentual=True)

In [14]:
fig_roomtype_quant.show()
fig_roomtype_percentual.show()

In [15]:
fig_roomtype_quant.write_image(
    "../results/presentation_figures/roomtype_quant.png",
    scale=3,
    width=800,
    height=800
)

fig_roomtype_percentual.write_image(
    "../results/presentation_figures/roomtype_percentual.png",
    scale=3,
    width=800,
    height=800
)

## Linhas de tempo

In [16]:
def preparar_colunas_tempo(df, data_col='last_review'):
    df[data_col] = pd.to_datetime(df[data_col], errors='coerce')
    df = df.assign(
        year=df[data_col].dt.year,
        quarter=df[data_col].dt.quarter,
        month=df[data_col].dt.month,
        day=df[data_col].dt.day
    )
    return df

In [17]:
def calcular_metricas_relativas(df):
    df_rel = {}

    df_rel["Dia"] = (
        df.groupby("day", as_index=False)
        .agg(
            preco_medio=('price', 'mean'),
            disponibilidade_media=('availability_365', 'mean')
        )
        .sort_values("day")
    )

    df_rel["Mês"] = (
        df.groupby("month", as_index=False)
        .agg(
            preco_medio=('price', 'mean'),
            disponibilidade_media=('availability_365', 'mean')
        )
        .sort_values("month")
    )

    df_rel["Trimestre"] = (
        df.groupby("quarter", as_index=False)
        .agg(
            preco_medio=('price', 'mean'),
            disponibilidade_media=('availability_365', 'mean')
        )
        .sort_values("quarter")
    )

    df_rel["Ano"] = (
        df.groupby("year", as_index=False)
        .agg(
            preco_medio=('price', 'mean'),
            disponibilidade_media=('availability_365', 'mean')
        )
        .sort_values("year")
    )

    return df_rel

In [18]:
def normalizar_metricas_0a100(df, colunas, id_col):
    df_norm = df.copy()
    scaler = MinMaxScaler(feature_range=(0, 100))
    df_norm[colunas] = scaler.fit_transform(df[colunas])

    df_norm = df_norm.melt(id_vars=[id_col], var_name="métrica", value_name="valor_normalizado")
    return df_norm

In [19]:
def plot_metricas_temporais(df, x, titulo, normalizado=False, cores=None):
    """
    Cria gráfico de linha para métricas temporais.
    
    Args:
        df: DataFrame com os dados
        x: Nome da coluna temporal
        titulo: Título do gráfico
        normalizado: Se True, usa dados normalizados
        cores: Lista de cores para as linhas
    """
    cores = cores or ["#2E86C1", "#FFA07A"]

    if normalizado:
        # Se dados já estiverem no formato longo normalizado
        df_plot = df
        y = "valor_normalizado"
    else:
        # Se dados estiverem no formato wide, converter para longo
        df_plot = df.melt(id_vars=[x], var_name="métrica", value_name="valor")
        y = "valor"

    fig = px.line(
        df_plot,
        x=x,
        y=y,
        color="métrica",
        markers=True,
        color_discrete_sequence=cores,
        title=titulo
    )

    fig.update_traces(line=dict(width=3), marker=dict(size=6))
    fig.update_layout(
        height=400,
        width=1000,
        paper_bgcolor='rgba(0,0,0,0)',
        plot_bgcolor='rgba(0,0,0,0)',
        font=dict(family="Fira Sans, Roboto", size=14, color="#2e2e2e"),
        title_font=dict(size=20, family="Fira Sans, Roboto", color="#111"),
        legend=dict(
            orientation="h",
            yanchor="bottom",
            y=1.05,
            xanchor="right",
            x=1,
            title=None
        ),
        xaxis=dict(showgrid=False, zeroline=False),
        yaxis=dict(
            showgrid=True,
            gridcolor="#EEE",
            zeroline=False,
            title="Valor normalizado (0-100)" if normalizado else "Valor"
        ),
        margin=dict(l=60, r=40, t=60, b=40)
    )
    return fig

In [20]:
# Preparar dados temporais
df_clean = preparar_colunas_tempo(df_reviews_rooms)

# Calcular métricas relativas para diferentes períodos
df_rel = calcular_metricas_relativas(df_clean)

# Definir métricas para normalização
metrics = ['preco_medio', 'disponibilidade_media']

# Criar versões normalizadas para cada período
df_plot = {}
for periodo, df in df_rel.items():
    x_column = {
        'Dia': 'day',
        'Mês': 'month',
        'Trimestre': 'quarter',
        'Ano': 'year'
    }[periodo]
    
    df_plot[periodo] = normalizar_metricas_0a100(df, metrics, x_column)

# Criar gráficos para cada período
fig_dia = plot_metricas_temporais(df_rel["Dia"], "day", "Média diária — Preço e Disponibilidade")
fig_mes = plot_metricas_temporais(df_rel["Mês"], "month", "Média mensal — Preço e Disponibilidade")
fig_trim = plot_metricas_temporais(df_rel["Trimestre"], "quarter", "Média trimestral — Preço e Disponibilidade")
fig_ano = plot_metricas_temporais(df_rel["Ano"], "year", "Média anual — Preço e Disponibilidade")

In [21]:
# Criar gráficos normalizados para cada período
fig_dia_norm = plot_metricas_temporais(
    df_plot["Dia"], "day",
    "Evolução normalizada - Média diária",
    normalizado=True
)
fig_mes_norm = plot_metricas_temporais(
    df_plot["Mês"], "month",
    "Evolução normalizada - Média mensal",
    normalizado=True
)
fig_trim_norm = plot_metricas_temporais(
    df_plot["Trimestre"], "quarter",
    "Evolução normalizada - Média trimestral",
    normalizado=True
)
fig_ano_norm = plot_metricas_temporais(
    df_plot["Ano"], "year",
    "Evolução normalizada - Média anual",
    normalizado=True
)

# Mostrar os gráficos normalizados
fig_dia_norm.show()
fig_mes_norm.show()
fig_trim_norm.show()
fig_ano_norm.show()

In [22]:
def exportar_figura(fig, nome, pasta="../results/presentation_figures", scale=3):
    caminho = f"{pasta}/{nome}.png"
    fig.write_image(
        caminho,
        scale=scale,
        width=1200,
        height=400
    )
    print(f"✅ Figura salva em: {caminho}")

exportar_figura(fig_dia_norm, "media_dia_preco_disponibilidade")
exportar_figura(fig_mes_norm, "media_mes_preco_disponibilidade")
exportar_figura(fig_trim_norm, "media_trimestre_preco_disponibilidade")
exportar_figura(fig_ano_norm, "media_ano_preco_disponibilidade")


✅ Figura salva em: ../results/presentation_figures/media_dia_preco_disponibilidade.png
✅ Figura salva em: ../results/presentation_figures/media_mes_preco_disponibilidade.png
✅ Figura salva em: ../results/presentation_figures/media_trimestre_preco_disponibilidade.png
✅ Figura salva em: ../results/presentation_figures/media_ano_preco_disponibilidade.png


In [23]:
def calcular_avaliacoes_relativas(df):
    """
    Calcula a média de avaliações (number_of_reviews) por unidade temporal
    considerando todos os anos.
    """
    df_rel = {}

    # Média por dia
    df_rel["Dia"] = (
        df.groupby("day", as_index=False)
        .agg(media_avaliacoes=('number_of_reviews', 'mean'))
        .sort_values("day")
    )

    # Média por mês
    df_rel["Mês"] = (
        df.groupby("month", as_index=False)
        .agg(media_avaliacoes=('number_of_reviews', 'mean'))
        .sort_values("month")
    )

    # Média por trimestre
    df_rel["Trimestre"] = (
        df.groupby("quarter", as_index=False)
        .agg(media_avaliacoes=('number_of_reviews', 'mean'))
        .sort_values("quarter")
    )

    # Média por ano
    df_rel["Ano"] = (
        df.groupby("year", as_index=False)
        .agg(media_avaliacoes=('number_of_reviews', 'mean'))
        .sort_values("year")
    )

    return df_rel

def plot_avaliacoes_temporais(df, x, titulo, cor=PALETA_THEME_COLORS[3]):
    """
    Cria gráfico de linha única para a média de avaliações por período.
    """
    fig = px.line(
        df,
        x=x,
        y="media_avaliacoes",
        markers=True,
        title=titulo,
        color_discrete_sequence=[cor]
    )

    fig.update_traces(line=dict(width=3), marker=dict(size=6))
    fig.update_layout(
        height=400,
        width=1000,
        paper_bgcolor='rgba(0,0,0,0)',
        plot_bgcolor='rgba(0,0,0,0)',
        font=dict(family="Fira Sans, Roboto", size=14, color="#2e2e2e"),
        title_font=dict(size=20, family="Fira Sans, Roboto", color="#111"),
        xaxis=dict(showgrid=False, zeroline=False),
        yaxis=dict(showgrid=True, gridcolor="#EEE", zeroline=False),
        margin=dict(l=60, r=40, t=60, b=40)
    )
    return fig

# Preparar colunas temporais (caso ainda não tenha feito)
df_clean = preparar_colunas_tempo(df_reviews_rooms)

# Calcular médias relativas da métrica number_of_reviews
df_avaliacoes = calcular_avaliacoes_relativas(df_clean)

# Gerar os gráficos
fig_dia = plot_avaliacoes_temporais(df_avaliacoes["Dia"], "day", "Média diária de avaliações")
fig_mes = plot_avaliacoes_temporais(df_avaliacoes["Mês"], "month", "Média mensal de avaliações")
fig_trim = plot_avaliacoes_temporais(df_avaliacoes["Trimestre"], "quarter", "Média trimestral de avaliações")
fig_ano = plot_avaliacoes_temporais(df_avaliacoes["Ano"], "year", "Média anual de avaliações")

# Exibir
fig_dia.show()
fig_mes.show()
fig_trim.show()
fig_ano.show()

In [24]:
exportar_figura(fig_dia, "media_dia_avaliacoes")
exportar_figura(fig_mes, "media_mes_avaliacoes")
exportar_figura(fig_trim, "media_trimestre_avaliacoes")
exportar_figura(fig_ano, "media_ano_avaliacoes")

✅ Figura salva em: ../results/presentation_figures/media_dia_avaliacoes.png
✅ Figura salva em: ../results/presentation_figures/media_mes_avaliacoes.png
✅ Figura salva em: ../results/presentation_figures/media_trimestre_avaliacoes.png
✅ Figura salva em: ../results/presentation_figures/media_ano_avaliacoes.png
